In [0]:
from functools import reduce
from pyspark.sql import Row
from pyspark import SparkConf, SparkContext, SQLContext
from pyspark.sql import SparkSession
from pyspark.sql.types import StringType, FloatType, DoubleType, StructType, StructField
from pyspark.sql.functions import udf, array
from pyspark.sql import functions as F
from pyspark.sql.functions import explode, col, lit, udf, mean as _mean, stddev as _stddev, log, log10, isnan, when, count, sqrt, greatest, least

from pyspark.mllib.tree import DecisionTree
from pyspark.ml.classification import RandomForestClassifier, LogisticRegression

from pyspark.ml.feature import VectorAssembler, StandardScaler
import time

In [0]:
# File location and type
train_features_location = "/FileStore/tables/train_features.csv"
train_scored_location = "/FileStore/tables/train_targets_scored-1.csv"

# CSV options
infer_schema = "true"
first_row_is_header = "true"
delimiter = ","
file_type = "csv"


# The applied options are for CSV files. For other file types, these will be ignored.
features_df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(train_features_location)

labels_df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(train_scored_location)

display(features_df)
display(labels_df)

sig_id 5-alpha_reductase_inhibitor 11-beta-hsd1_inhibitor acat_inhibitor acetylcholine_receptor_agonist acetylcholine_receptor_antagonist acetylcholinesterase_inhibitor adenosine_receptor_agonist adenosine_receptor_antagonist adenylyl_cyclase_activator adrenergic_receptor_agonist adrenergic_receptor_antagonist akt_inhibitor aldehyde_dehydrogenase_inhibitor alk_inhibitor ampk_activator analgesic androgen_receptor_agonist androgen_receptor_antagonist anesthetic_-_local angiogenesis_inhibitor angiotensin_receptor_antagonist anti-inflammatory antiarrhythmic antibiotic anticonvulsant antifungal antihistamine antimalarial antioxidant antiprotozoal antiviral apoptosis_stimulant aromatase_inhibitor atm_kinase_inhibitor atp-sensitive_potassium_channel_antagonist atp_synthase_inhibitor atpase_inhibitor atr_kinase_inhibitor aurora_kinase_inhibitor autotaxin_inhibitor bacterial_30s_ribosomal_subunit_inhibitor bacterial_50s_ribosomal_subunit_inhibitor bacterial_antifolate bacterial_cell_wall_synthesis_inhibitor bacterial_dna_gyrase_inhibitor bacterial_dna_inhibitor bacterial_membrane_integrity_inhibitor bcl_inhibitor bcr-abl_inhibitor benzodiazepine_receptor_agonist beta_amyloid_inhibitor bromodomain_inhibitor btk_inhibitor calcineurin_inhibitor calcium_channel_blocker cannabinoid_receptor_agonist cannabinoid_receptor_antagonist carbonic_anhydrase_inhibitor casein_kinase_inhibitor caspase_activator catechol_o_methyltransferase_inhibitor cc_chemokine_receptor_antagonist cck_receptor_antagonist cdk_inhibitor chelating_agent chk_inhibitor chloride_channel_blocker cholesterol_inhibitor cholinergic_receptor_antagonist coagulation_factor_inhibitor corticosteroid_agonist cyclooxygenase_inhibitor cytochrome_p450_inhibitor dihydrofolate_reductase_inhibitor dipeptidyl_peptidase_inhibitor diuretic dna_alkylating_agent dna_inhibitor dopamine_receptor_agonist dopamine_receptor_antagonist egfr_inhibitor elastase_inhibitor erbb2_inhibitor estrogen_receptor_agonist estrogen_receptor_antagonist faah_inhibitor farnesyltransferase_inhibitor fatty_acid_receptor_agonist fgfr_inhibitor flt3_inhibitor focal_adhesion_kinase_inhibitor free_radical_scavenger fungal_squalene_epoxidase_inhibitor gaba_receptor_agonist gaba_receptor_antagonist gamma_secretase_inhibitor glucocorticoid_receptor_agonist glutamate_inhibitor glutamate_receptor_agonist glutamate_receptor_antagonist gonadotropin_receptor_agonist gsk_inhibitor hcv_inhibitor hdac_inhibitor histamine_receptor_agonist histamine_receptor_antagonist histone_lysine_demethylase_inhibitor histone_lysine_methyltransferase_inhibitor hiv_inhibitor hmgcr_inhibitor hsp_inhibitor igf-1_inhibitor ikk_inhibitor imidazoline_receptor_agonist immunosuppressant insulin_secretagogue insulin_sensitizer integrin_inhibitor jak_inhibitor kit_inhibitor laxative leukotriene_inhibitor leukotriene_receptor_antagonist lipase_inhibitor lipoxygenase_inhibitor lxr_agonist mdm_inhibitor mek_inhibitor membrane_integrity_inhibitor mineralocorticoid_receptor_antagonist monoacylglycerol_lipase_inhibitor monoamine_oxidase_inhibitor monopolar_spindle_1_kinase_inhibitor mtor_inhibitor mucolytic_agent neuropeptide_receptor_antagonist nfkb_inhibitor nicotinic_receptor_agonist nitric_oxide_donor nitric_oxide_production_inhibitor nitric_oxide_synthase_inhibitor norepinephrine_reuptake_inhibitor nrf2_activator opioid_receptor_agonist opioid_receptor_antagonist orexin_receptor_antagonist p38_mapk_inhibitor p-glycoprotein_inhibitor parp_inhibitor pdgfr_inhibitor pdk_inhibitor phosphodiesterase_inhibitor phospholipase_inhibitor pi3k_inhibitor pkc_inhibitor potassium_channel_activator potassium_channel_antagonist ppar_receptor_agonist ppar_receptor_antagonist progesterone_receptor_agonist progesterone_receptor_antagonist prostaglandin_inhibitor prostanoid_receptor_antagonist proteasome_inhibitor protein_kinase_inhibitor protein_phosphatase_inhibitor protein_synthesis_inhibitor protein_tyrosine_kinase_inhibitor radiopaque_medium raf_inhibitor ras_gtpase_inhibi

In [0]:
feature_rows = features_df.count()
label_rows = labels_df.count()
print('# of feature rows: ', feature_rows)
print('# of label rows: ', label_rows)

# Check for number of duplicate rows
duplicates = features_df.groupBy(features_df.columns).count().where(F.col('count') > 1).select(F.sum('count').alias('Duplicate Row Count')).collect()

# Check for number of rows with for missing value columns
dropped_na_feature_df = features_df.dropna(how="any", thresh=None, subset=None)
num_missing_rows = features_df.count() - dropped_na_feature_df.count()

num_duplicate_rows = 0 if duplicates[0].__getitem__("Duplicate Row Count")==None else duplicates[0].__getitem__("Duplicate Row Count")

print('Number of duplicate rows in features dataframe: ', num_duplicate_rows)
print('Number of rows with missing value in features dataframe: ', num_missing_rows)

# of feature rows: 23814
# of label rows: 23814
Number of duplicate rows in features dataframe: 0
Number of rows with missing value in features dataframe: 0

In [0]:
'''
Data Processing: 
  - Clean Dataframe(drop useless rows: cp_type=ctrl) 
  - Feature Selection (based on importance of RF model) can use other features
'''
features_df = features_df.filter((features_df.cp_type == 'trt_cp'))
top_18_features = ['sig_id', 'c-98', 'c-65', 'c-17', 'c-70', 'g-392', 'g-100', 'c-53', 'g-628', 'g-91', 'c-6', 'c-32', 'c-85', 'g-75', 'g-175', 'g-385', 'cp_dose', 'cp_time']
df = features_df.select([c for c in features_df.columns if c in top_18_features])
display(df)

sig_id cp_time cp_dose g-75 g-91 g-100 g-175 g-385 g-392 g-628 c-6 c-17 c-32 c-53 c-65 c-70 c-85 c-98 id_000644bb2 24 D1 -0.6332 -1.123 -0.5364 -1.413 1.76 -0.1301 -0.8976 0.2888 -0.2798 0.3817 0.0471 0.1403 -0.0553 0.1799 0.3801 id_000779bfc 72 D1 -0.5857 -0.3854 0.7129 0.2697 -0.1022 0.0452 -0.0585 0.2835 -0.2274 0.1888 0.2111 0.4151 -0.0765 0.442 0.6077 id_000a6266a 48 D1 -1.357 0.4286 -0.7646 1.187 -1.112 -0.228 0.662 -0.7513 0.0643 0.1171 0.7047 -2.364 0.1682 0.1172 -1.408 id_0015fd391 48 D1 -3.321 4.916 1.039 3.458 1.317 5.391 2.825 -2.583 -0.5252 0.067 -1.367 -1.493 -1.187 -1.539 -0.3876 id_001626bd3 72 D2 -0.7868 0.8025 0.0968 0.5282 -1.166 -0.5027 -0.6423 -0.0852 -0.5176 0.5227 -0.229 0.3973 0.1813 0.0698 -0.3786 id_001762a82 24 D1 -0.2243 0.4944 -1.522 -0.0131 0.6992 -0.8619 0.0522 1.334 1.436 1.185 1.494 2.002 0.6596 0.698 0.7848 id_001bd861f 24 D2 3.375 1.58 4.491 1.624 -4.608 4.843 1.978 1.048 0.9935 1.335 -0.3832 0.5135 0.2662 -0.423 0.1351 id_0020d0484 48 D1 2.021 1.232 0.7365 2.385 -1.884 2.807 1.533 -0.2375 0.2757 -0.2019 0.6213 0.2156 -0.1342 0.1194 -0.9622 id_00224bf20 48 D1 1.179 -0.7994 -0.2113 -0.1636 1.063 -0.1412 -0.0318 -0.4887 -0.9109 -0.8075 -0.4742 -0.4082 -0.6872 -0.009 -0.642 id_0023f063e 48 D2 0.1832 0.2758 -0.0175 -0.1438 0.1179 0.2637 -0.8548 -0.8989 -0.4817 -0.5435 -0.9559 -0.9295 0.1205 -0.3377 0.0189 id_002452c7e 72 D2 0.5304 0.4167 -0.3339 -0.6787 1.038 1.189 0.0682 -1.186 -1.986 0.6031 0.4875 0.4413 1.278 0.7488 -0.0125 id_0024bcd70 48 D2 -0.1323 -0.0766 -0.7517 0.3091 0.7447 -0.9902 -0.2628 -0.251 0.3168 -0.0545 0.8724 0.0469 0.1501 -1.068 0.8285 id_0025c5949 48 D1 0.1423 -1.342 -0.0107 -0.2238 1.044 0.5452 0.0901 0.9666 0.2611 0.8004 0.9733 0.0983 0.1707 0.0049 0.3453 id_00289dc6e 48 D2 0.8291 0.8568 0.6891 -0.3304 -1.487 -1.15 -0.93 -0.0688 -0.0191 0.651 0.6921 0.4829 -0.5976 0.6261 0.7842 id_002d31e2c 72 D1 -5.878 -0.9851 0.6251 -0.1684 -0.6436 0.6662 3.414 -5.561 -9.97 0.6426 -3.549 -9.448 -6.887 -3.321 -6.239 id_002e08ff8 48 D1 0.4821 -0.2988 1.084 0.5408 -0.4462 0.2168 -0.8637 0.4515 1.359 0.3772 0.3884 0.6421 0.2717 -0.0242 0.7705 id_002fb9c19 48 D1 -10.0 10.0 9.68 -3.959 -5.514 3.793 2.56 -10.0 -10.0 -9.859 -10.0 -10.0 -10.0 -9.984 -9.984 id_0031dd989 24 D2 -1.241 0.4236 0.1346 0.4696 0.2006 0.4668 0.4757 1.35 0.8049 0.1373 0.8424 0.4971 0.6656 0.8037 0.4259 id_003603254 72 D2 -1.318 2.661 0.7406 3.153 0.9531 2.71 0.7762 -2.04 0.0691 0.7908 -0.8597 -1.544 -1.498 0.0375 -0.0259 id_0036b0342 48 D1 -0.4743 0.4241 0.0691 -0.7524 0.3893 -0.014 -0.2428 0.4829 -0.0792 0.3639 0.0707 -0.4321 0.3752 0.7881 0.4251 id_0039a2ff9 48 D2 0.1487 -0.6802 -0.0538 -1.244 0.0637 -0.8389 -0.9302 0.4703 0.0254 0.7494 0.4263 -1.688 -0.6442 0.1642 -0.0019 id_003b43239 48 D1 0.8338 -0.7404 0.7068 0.1671 0.8496 -0.86 -0.8195 0.3103 -0.0565 -0.2507 -0.209 0.349 -0.8978 -0.3735 0.8025 id_003d4b6f0 72 D1 0.9231 -0.5132 3.851 -2.477 -0.9002 0.2035 0.0122 0.1174 -0.2678 -0.4055 -0.4205 0.4505 -0.3422 0.4561 -0.3555 id_003fdd734 72 D1 -0.0982 -0.2489 -0.4236 0.9062 -0.015 -0.4638 0.5946 0.5405 0.6428 0.2708 1.049 0.1612 0.352 0.5864 -0.2095 id_00505b3c8 72 D2 -0.1612 1.157 9.221 -6.141 -2.516 -0.7268 0.9851 0.0236 -0.9775 -0.1575 2.061 0.1079 0.3227 0.4508 0.3978 id_00548fd5c 72 D1 -0.5956 0.3143 0.1863 -0.4082 -0.2248 -0.2283 -0.0253 0.5039 0.0968 0.6646 1.103 0.7542 0.4723 1.27 0.6742 id_00578737a 48 D2 1.091 -0.2866 -0.4156 0.1411 0.6524 0.3834 -0.5538 0.8177 0.6759 0.6873 0.4191 0.2042 1.003 0.8232 0.3273 id_005c3cb48 48 D1 -0.4584 -0.6594 -0.3403 0.0182 0.5148 0.7113 0.0 -0.77 0.6063 -0.7644 0.9233 -0.6175 0.4113 0.3239 0.2554 id_005c3ee1a 72 D1 1.246 -0.9868 1.258 1.12 -0.3956 -1.353 -0.1633 0.3367 0.4753 0.1824 1.416 -0.6283 0.3889 0.6152 -0.1502 id_0062bfc63 72 D1 0.4328 -1.931 0.2025 1.656 -0.5159 -1.093 -1.179 -0.4982 0.2218 0.1944 0.5507 -1.621 0.3925 0.1503 -0.5519 id_0063cd461 48 D2 0.2398 0.2261 -0.1693 0.1359 0.8044 0.0 -0.1849 -0.3797 -0.1139 -0.4139 -0.0576 -0.1102 -0.6793 -0.1658 -0.2453 id_006e

In [0]:
# engineer something with cp_time and cp_dose (maybe as combination?)
'''
Feature Engineering: create statistic features
 - row sum, mean, max, min, std, for g, c, gc
'''
g_features = [feature for feature in df.columns if 'g-' in feature]
c_features = [feature for feature in df.columns if 'c-' in feature]
gc_features = g_features + c_features

df = df.withColumn("g_mean", reduce(lambda x,y: x+y, (col(x) for x in g_features)) / len(g_features))
df = df.withColumn("c_mean", reduce(lambda x,y: x+y, (col(x) for x in c_features)) / len(c_features))
df = df.withColumn("gc_mean", reduce(lambda x,y: x+y, (col(x) for x in gc_features)) / len(gc_features))

df = df.withColumn("g_std", sqrt(reduce(lambda x,y: x-col('g_mean') + y-col('g_mean'), (col(x) for x in g_features))**2 / len(g_features)))
df = df.withColumn("c_std", sqrt(reduce(lambda x,y: x-col('c_mean') + y-col('c_mean'), (col(x) for x in c_features))**2 / len(c_features)))
df = df.withColumn("gc_std", sqrt(reduce(lambda x,y: x-col('gc_mean') + y-col('gc_mean'), (col(x) for x in gc_features))**2 / len(gc_features)))

df = df.withColumn("g_sum", reduce(lambda x,y: x+y, (col(x) for x in g_features)))
df = df.withColumn("c_sum", reduce(lambda x,y: x+y, (col(x) for x in c_features)))
df = df.withColumn("gc_sum", reduce(lambda x,y: x+y, (col(x) for x in gc_features)))

df = df.withColumn("g_max", reduce(lambda x,y: greatest(x,y), g_features))
df = df.withColumn("c_max", reduce(lambda x,y: greatest(x,y), c_features))
df = df.withColumn("gc_max", reduce(lambda x,y: greatest(x,y), gc_features))

df = df.withColumn("g_min", reduce(lambda x,y: least(x,y), g_features))
df = df.withColumn("c_min", reduce(lambda x,y: least(x,y), c_features))
df = df.withColumn("gc_min", reduce(lambda x,y: least(x,y), gc_features))


engineered_features = ["g_mean", "c_mean", "gc_mean", "g_std", "c_std", "gc_std", "g_sum", "c_sum", "gc_sum", "g_max", "c_max", "gc_max", "g_min", "c_min", "gc_min",]

"""
One-Hot-Encoder
  for cp_dose; create the one-hot-vector then drop the original categorical vector
"""
def cp_dose_map(val):
  if val == 'D1':
    return 1
  if val == 'D2':
    return 0
  
dose_udf = udf(cp_dose_map)

df = df.withColumn("dose_one_hot", dose_udf("cp_dose"))
df = df.withColumn("dose_one_hot", df["dose_one_hot"].cast(DoubleType()))
df = df.drop('cp_dose')

In [0]:
# Labels are assembled into one vector. Each cell is a tuple: (length of labels, index of existing value, value)
# assembled_labels_df.select('labels').show()
features = df.columns
features.remove('sig_id')

'''
Feature Vectors Assembler (required)
 - assembles all features into one vector. Each row in the assembled vector is a tuple of all the features
 - using also the one-hot-encoded features in the assembly
'''
features_assembler = VectorAssembler(inputCols=features, outputCol="assembledFeatures")
df = features_assembler.transform(df)

In [0]:
# create a 'train' dataframe: both features and labels
trainingData = df.join(labels_df, on=['sig_id'], how='inner')

'''
Label Vectors Assembler
'''
labels_assembler = VectorAssembler(inputCols=labels_df.columns[1:], outputCol="assembledLabels")
trainingData = labels_assembler.transform(trainingData)

'''
Assemble both feature and label vectors for clustering
  Only for KNN cluster algorithm
  Drop after KNN
'''
feature_label_assembler = VectorAssembler(inputCols=["assembledFeatures", "assembledLabels"], outputCol="assemebled")
trainingData = feature_label_assembler.transform(trainingData)


'''
KMeans clustering - engineer new feature based on cluster results
Used K=6 to fit the assembled features, KNN returned 4 cluster classes.

Include the labels and see what happens - same thing

What does the cluster numbers mean? IE: How to test the validity of the cluster results
'''
from pyspark.ml.clustering import KMeans
# kmeans = KMeans(k=6, featuresCol='assembledFeatures', predictionCol='clusterPrediction', initMode='k-means||', initSteps=2, tol=0.0001, maxIter=20, seed=None, distanceMeasure='euclidean', weightCol=None)
kmeans = KMeans(k=6, featuresCol='assemebled', predictionCol='clusterPrediction', distanceMeasure='euclidean',)
model = kmeans.fit(trainingData)
transformed = model.transform(trainingData).select("sig_id", "clusterPrediction")
# rows = transformed.collect()
summary = model.summary


# join the cluster prediction vector to the dataframe
df = df.join(transformed, on=['sig_id'], how='inner')
df = df.drop("assembledFeatures") # get rid of this assembledFeature column, and make another one without one-hot-encoded features for standardization


# Drop the 'assembled' column vector because we no longer need this (only for clustering)
# trainingData = trainingData.drop("assembled")
# trainingData = trainingData.drop("sig_id") # drop id before training


'''
Standardize/Normalization 
  This step is after feature engineering step, before Feature Selection
  Standardize features in df (dataframe with all the necessary features: original + feature engineered)
  **NOTE** - do not standardize one-hot-encoded labels or cluster labels
'''
df_features = df.columns
df_features.remove('sig_id')

# feature_labels = ["cp_time_onehot", "cp_dose_onehot", "clusterPrediction",] # list of features that we do not want to standardize. IE: one-hot-encoded vectors, cluster vector, ...
feature_labels = ["dose_one_hot", "clusterPrediction",] # list of features that we do not want to standardize. IE: one-hot-encoded vectors, cluster vector, ...
features_to_standardize = [feat_col for feat_col in df_features if feat_col not in feature_labels] # list of feature vectors we want to standardize

# assemble before standardizing
features_assembler = VectorAssembler(inputCols=features_to_standardize, outputCol="assembledFeatures")
df = features_assembler.transform(df)

scaler = StandardScaler(inputCol="assembledFeatures", outputCol="assembledScaledFeatures")
df = scaler.fit(df).transform(df)


# Assemble feature_labels and assembledScaledFeatures
feature_labels.append("assembledScaledFeatures")
features_assembler = VectorAssembler(inputCols=feature_labels, outputCol="allFeatures")
df = features_assembler.transform(df)



aasembled_train = df.select("sig_id", "allFeatures")
display(aasembled_train)

"""
Feature Selection goes here
"""


"""
** Do a final round of assembling for feature vectors

For training - Need to assemble: assembledScaledFeatures & clusterPrediction vectors before fitting a learner on assembledLabels
"""
# features_assembler = VectorAssembler(inputCols=["assembledScaledFeatures", "clusterPrediction"], outputCol="allFeatures")
# trainingData = features_assembler.transform(trainingData)

--------------------------------------------------------------------------- 
 NameError Traceback (most recent call last)
 <command-3348806284208672> in <module> 
 73 
 74 aasembled_train = df . select ( "sig_id" , "allFeatures" ) 
 ---> 75 display ( assembled_train ) 
 76 """
 77 Feature Selection goes here

 NameError : name 'assembled_train' is not defined

In [0]:
display(aasembled_train)


sig_id allFeatures id_000644bb2 List(1, 33, List(), List(1.0, 2.0, 1.2368650097727056, -0.2737066921494381, -0.5734680814668819, -0.24356451261839523, -0.8456710759796818, 0.9322994272077685, -0.06347510666600883, -0.7465676683439648, 0.1251957216140379, -0.1305412989454399, 0.20875095602902383, 0.02606952407800695, 0.06105621528662336, -0.02445615521331749, 0.09256787593636896, 0.2012491488069956, -0.6234982412415624, 0.07038344624763396, -0.12300266548920595, 0.7554046976258204, 0.07488954360851474, 0.133068028474023, -0.6234982412415624, 0.07038344624763396, -0.123002665489206, 0.7396021913775526, 0.2298149895598879, 0.7698510193070086, -0.6801574856910926, -0.12240125853979449, -0.6140053087986103)) id_000779bfc List(1, 33, List(), List(1.0, 0.0, 3.710595029318117, -0.2531743676435974, -0.19680730062095841, 0.3237083166399216, 0.1614136512326399, -0.054136932648087464, 0.022052842592648725, -0.04865664950771162, 0.1228981547007609, -0.10609396490419239, 0.10325433717128556, 0.11684238923285067, 0.18064458279028764, -0.033831751786958186, 0.22743191308435284, 0.32175508479350495, -0.021808703154448775, 0.11988196334919778, 0.11323011835539017, 0.02642252330847392, 0.12755706065495373, 0.122495789449004, -0.02180870315444878, 0.11988196334919778, 0.11323011835539022, 0.2995809103596916, 0.3658856933600836, 0.3118334043545264, -0.2819308134248216, -0.0994783638025349, -0.2545101977093744)) id_000a6266a List(1, 33, List(), List(1.0, 1.0, 2.4737300195454113, -0.5865760916721218, 0.2188676934253834, -0.34718386716634037, 0.7104115832893717, -0.5890437290085446, -0.11124000245849358, 0.5506102901556426, -0.325690947536796, 0.02999930493992775, 0.06404175255697848, 0.39004657362572176, -1.0287732924987711, 0.0743856294191682, 0.06030547559612252, -0.7454848764016042, -0.2482836974506474, -0.2178714768496671, -0.2951153081861626, 0.3008102653580102, 0.2318200704350017, 0.31926472549720886, -0.2482836974506474, -0.2178714768496671, -0.2951153081861627, 0.4988112506620198, 0.42428772109733565, 0.5192120226803518, -0.6532014919198957, -1.034155022116062, -1.0272530431704987)) id_0015fd391 List(1, 33, List(), List(1.0, 1.0, 2.4737300195454113, -1.4355336775557233, 2.510390995985033, 0.47178137324853214, 2.069589936827841, 0.6976354236549039, 2.630240584446223, 2.349658715543339, -1.119738742829155, -0.2450332030241066, 0.036642164144471044, -0.7566250406504351, -0.6497286487735472, -0.5249449590995996, -0.791895281078776, -0.20522012648669163, 3.2765479498871324, -0.5859740406660241, 0.4300831628758261, 3.9697300643740774, 0.6234893403417429, 0.46527705994127855, 3.276547949887133, -0.5859740406660241, 0.43008316287582626, 2.265451939611583, 0.0403395449319164, 2.358106161979593, -1.5985867020383004, -1.1299587234034638, -1.4431080187687082)) id_001626bd3 List(1, 33, List(), List(0.0, 0.0, 3.710595029318117, -0.3401017457093776, 0.4098024357766453, 0.043954222262230905, 0.3161241771638131, -0.6176483705251465, -0.24526468963107334, -0.5342250594667208, -0.036934471888905925, -0.24148740648377298, 0.2858635701241047, -0.12674991536865374, 0.1728983202663967, 0.0801790405094839, 0.035915718401103684, -0.20045495327105636, -0.35026035460457455, -0.0025545524912560136, -0.11123266697717349, 0.4243609680975373, 0.002718100354464933, 0.12033488573350411, -0.3502603546045746, -0.0025545524912560136, -0.11123266697717356, 0.33723338555709426, 0.3147086587449658, 0.35102581988288317, -0.5612622988788492, -0.22642920450392287, -0.5066738783150598)) id_001762a82 List(1, 33, List(), List(1.0, 2.0, 1.2368650097727056, -0.09695579761389603, 0.2524689398728641, -0.6910984120156554, -0.007840262629394077, 0.3703771360816317, -0.4205164829779632, 0.043416702637650365, 0.5782932570399121, 0.6699689252525077, 0.6480740971820624, 0.8269186618374178, 0.8712369422937987, 0.29170488207421724, 0.35915718401103686, 0.41552310440339424, -0.2884410691244641, 0.6235838134762207, 0.5346858528028277, 0.3494632770269789, 0.6635069704967916, 0.5784394346451588, -0.28

In [0]:
from pyspark.ml.classification import LogisticRegression, RandomForestClassifier
from pyspark.ml import Pipeline

'''
Binary Relevance - logistic on each target
'''
# loop through each label and train a logistic regression model on the train data that classifies that label
# model_dict = dict()
# start_time = time.time()

# for ind, label in enumerate(labels_df.columns[1:]):
#   sub_start_time = time.time()
#   print(f'Training on label {ind}: {label}')
#   lr = LogisticRegression(featuresCol = 'assembledFeatures', labelCol = label, maxIter=15)
#   pipeline = Pipeline(stages=[lr])
#   sub_model = pipeline.fit(trainingData)
  
#   elapsed_time = time.time() - sub_start_time
#   print(f'Training time for: {label}, {elapsed_time}s')
  
#   model_dict[label] = {
#     'model': lr,
#     'time': elapsed_time
#   }
  
#   lr.save_model()
#   print(f'Total elapsed time: {time.time()-start_time}s\n')

In [0]:
'''
This doesn't work, haven't figured out how to write a trained model to file
'''
import pickle

for key, val in model_dict.items():
  print(key)
  model = val['model']
  file_name = '/tmp/ml_python_model_export/logit_' + key + '.pkl'
  
  with open(file_name, 'wb') as f:
    pickle.dumps(model, f)
    
  ModelExport.exportModel(model, f"/tmp/ml_python_model_export/{file_name}")